In [30]:
from numpy import expand_dims
from numpy import ones
from numpy import zeros
from numpy.random import rand
from numpy.random import randint
from keras.datasets.mnist import load_data
from keras.optimizers import Adam
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Conv2D
from keras.layers import Flatten
from keras.layers import Dropout
from keras.layers import LeakyReLU

In [31]:
def define_discriminator(in_shape=(28,28,1)):
    model = Sequential()
    model.add(Conv2D(64, (3,3), strides=(2, 2), padding='same', input_shape=in_shape))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dropout(0.4))
    model.add(Conv2D(64, (3,3), strides=(2, 2), padding='same'))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dropout(0.4))
    model.add(Flatten())
    model.add(Dense(1, activation='sigmoid'))
    # compile model
    opt = Adam(learning_rate=0.0002, beta_1=0.5)
    model.compile(loss='binary_crossentropy', optimizer=opt, metrics=['accuracy'])
    return model

In [32]:
# load and prepare mnist training images
def load_real_samples():
    # load mnist dataset
    (trainX, _), (_, _) = load_data()
    # expand to 3d, e.g. add channels dimension
    X = expand_dims(trainX, axis=-1)
    # convert from unsigned ints to floats
    X = X.astype('float32')
    # scale from [0,255] to [0,1]
    X = X / 255.0
    return X

In [33]:
# select real samples
def generate_real_samples(dataset, n_samples):
    # choose random instances
    ix = randint(0, dataset.shape[0], n_samples)
    # retrieve selected images
    X = dataset[ix]
    # generate 'real' class labels (1)
    y = ones((n_samples, 1))
    return X, y

In [34]:
# generate n fake samples with class labels
def generate_fake_samples(n_samples):
    # generate uniform random numbers in [0,1]
    X = rand(28 * 28 * n_samples)
    # reshape into a batch of grayscale images
    X = X.reshape((n_samples, 28, 28, 1))
    # generate 'fake' class labels (0)
    y = zeros((n_samples, 1))
    return X, y

In [35]:
# train the discriminator model
def train_discriminator(model, dataset, n_iter=100, n_batch=256):
    half_batch = int(n_batch / 2)
    # manually enumerate epochs
    for i in range(n_iter):
        # get randomly selected 'real' samples
        X_real, y_real = generate_real_samples(dataset, half_batch)
        # update discriminator on real samples
        _, real_acc = model.train_on_batch(X_real, y_real)
        # generate 'fake' examples
        X_fake, y_fake = generate_fake_samples(half_batch)
        # update discriminator on fake samples
        _, fake_acc = model.train_on_batch(X_fake, y_fake)
        # summarize performance
        print('>%d real=%.0f%% fake=%.0f%%' % (i+1, real_acc*100, fake_acc*100))

In [36]:
# define the discriminator model
model = define_discriminator()
# load image data
dataset = load_real_samples()
# fit the model
train_discriminator(model, dataset)

>1 real=48% fake=60%
>2 real=59% fake=65%
>3 real=64% fake=69%
>4 real=68% fake=71%
>5 real=70% fake=73%
>6 real=71% fake=74%
>7 real=73% fake=75%
>8 real=73% fake=75%
>9 real=74% fake=76%
>10 real=75% fake=76%
>11 real=76% fake=77%
>12 real=76% fake=77%
>13 real=76% fake=77%
>14 real=77% fake=78%
>15 real=78% fake=79%
>16 real=79% fake=79%
>17 real=79% fake=80%
>18 real=80% fake=81%
>19 real=81% fake=81%
>20 real=81% fake=82%
>21 real=82% fake=82%
>22 real=82% fake=83%
>23 real=83% fake=83%
>24 real=84% fake=84%
>25 real=84% fake=84%
>26 real=85% fake=85%
>27 real=85% fake=85%
>28 real=86% fake=86%
>29 real=86% fake=86%
>30 real=87% fake=87%
>31 real=87% fake=87%
>32 real=87% fake=88%
>33 real=88% fake=88%
>34 real=88% fake=88%
>35 real=88% fake=89%
>36 real=89% fake=89%
>37 real=89% fake=89%
>38 real=89% fake=89%
>39 real=90% fake=90%
>40 real=90% fake=90%
>41 real=90% fake=90%
>42 real=90% fake=90%
>43 real=91% fake=91%
>44 real=91% fake=91%
>45 real=91% fake=91%
>46 real=91% fake=9